In [3]:
import pandas as pd
import numpy as np
from catboost import CatBoostRegressor
import joblib
from tqdm import tqdm
import warnings
warnings.filterwarnings('ignore') #warning 문구 제거
pd.set_option('display.max_columns', None)

In [4]:
#데이터 불러오기
path = '/Users/takhaseon/Documents/KTB/project/TripPop/data'
# 각 CSV 파일 읽기
visit_area_info = pd.read_csv(path + '/visit_area_info.csv')
travel = pd.read_csv(path+'/travel.csv')
traveller_master = pd.read_csv(path+'/traveller.csv')

# 전처리

## 1) visit_area_info 방문지 정보 df

In [5]:
# 관광지 선택
visit_area_info = visit_area_info[ (visit_area_info['VISIT_AREA_TYPE_CD'] == 1) | 
                                  (visit_area_info['VISIT_AREA_TYPE_CD'] == 2) |
           (visit_area_info['VISIT_AREA_TYPE_CD'] == 3) | (visit_area_info['VISIT_AREA_TYPE_CD'] == 6) |
           (visit_area_info['VISIT_AREA_TYPE_CD'] == 7) | (visit_area_info['VISIT_AREA_TYPE_CD'] == 8) |
            (visit_area_info['VISIT_AREA_TYPE_CD'] == 13) ]

In [6]:
#인덱스 재정렬
visit_area_info = visit_area_info.reset_index(drop = True)

In [7]:
#제대로 추출되었는지 확인
visit_area_info['VISIT_AREA_TYPE_CD'].unique()

array([ 7,  3,  2,  8,  1,  6, 13])

In [8]:
visit_area_info.dropna(subset = ['LOTNO_ADDR'], inplace = True)
visit_area_info = visit_area_info.reset_index(drop = True)

In [9]:
# 시도/군구 변수 생성
sido = []
gungu = []
for i in range(len(visit_area_info['LOTNO_ADDR'])):
    sido.append(visit_area_info['LOTNO_ADDR'][i].split(' ')[0])
    gungu.append('세종시') if '세종' in visit_area_info['LOTNO_ADDR'][i].split(' ')[0] else gungu.append(visit_area_info['LOTNO_ADDR'][i].split(' ')[1])  
    

In [10]:
sido = ['서울특별시' if '서울' in place else '인천광역시' if '인천' in place else '대전광역시' if '대전' in place else '대구광역시' if '대구' in place else '부산광역시' if '부산' in place else
        '울산광역시' if '울산' in place else '광주광역시' if '광주' in place else '세종시' if '세종' in place else '경기도' if '경기' in place else '강원도' if '강원' in place else
        '경상북도' if '경북' in place else '경상남도' if '경남' in place else '전라북도' if '전북' in place else '전라남도' if '전남' in place else '충청북도' if '충북' in place else
        '충청남도' if '충남' in place else '제주도' if '제주' in place else place for place in sido]

print(sido)
print(gungu)

['경기도', '서울특별시', '경기도', '경기도', '서울특별시', '서울특별시', '경기도', '서울특별시', '서울특별시', '경기도', '경기도', '인천광역시', '경기도', '서울특별시', '경기도', '서울특별시', '경기도', '경기도', '서울특별시', '서울특별시', '서울특별시', '서울특별시', '서울특별시', '경기도', '서울특별시', '경기도', '서울특별시', '경기도', '경기도', '서울특별시', '경기도', '서울특별시', '강원도', '경기도', '강원도', '경기도', '경기도', '서울특별시', '서울특별시', '경기도', '경기도', '인천광역시', '서울특별시', '서울특별시', '경기도', '경기도', '경기도', '강원도', '서울특별시', '경기도', '서울특별시', '경기도', '서울특별시', '경기도', '경기도', '경기도', '경기도', '서울특별시', '경기도', '서울특별시', '서울특별시', '경기도', '경기도', '경기도', '서울특별시', '경기도', '경기도', '서울특별시', '경기도', '경기도', '서울특별시', '경기도', '경기도', '인천광역시', '경기도', '서울특별시', '인천광역시', '경기도', '서울특별시', '경기도', '경기도', '경기도', '인천광역시', '경기도', '경기도', '서울특별시', '경기도', '경기도', '서울특별시', '경기도', '경기도', '서울특별시', '경기도', '서울특별시', '경기도', '서울특별시', '인천광역시', '서울특별시', '서울특별시', '서울특별시', '강원도', '서울특별시', '서울특별시', '경기도', '서울특별시', '경기도', '서울특별시', '경기도', '서울특별시', '인천광역시', '경기도', '경기도', '강원도', '경기도', '경기도', '경기도', '서울특별시', '서울특별시', '서울특별시', '경기도', '광주광역시', '서울특별시', '경기도', '경기도', '서울특별시', '경기도', '서울

In [11]:
visit_area_info['SIDO'] = sido
visit_area_info['GUNGU'] = gungu

In [12]:
visit_area_info['GUNGU'].value_counts()

GUNGU
제주시     6700
서귀포시    5201
경주시     1301
중구      1128
전주시     1035
        ... 
강동구        7
양천구        6
영양군        6
중랑구        4
금천구        3
Name: count, Length: 206, dtype: int64

### 변수 선택

TRAVEL_ID 여행 ID

VISIT_AREA_NM 방문 장소 이름

SIDO 시/도

GUNGU 군/구

VISIT_AREA_TYPE_CD 관광 장소 유형

DGSTFN 만족도

REVISIT_INTENTION 재방문의향

RCMDTN_INTENTION 추천의향

RESIDENCE_TIME_MIN 체류시간분

REVISIT_YN 재방문여부

In [13]:
visit_area_info = visit_area_info[['TRAVEL_ID', 'VISIT_AREA_NM', 'SIDO', 'GUNGU', 'VISIT_AREA_TYPE_CD', 'DGSTFN',
                                  'REVISIT_INTENTION', 'RCMDTN_INTENTION', 'RESIDENCE_TIME_MIN', 'REVISIT_YN', 'VISIT_AREA_ID']]

## 2) travel 여행 정보 df

In [14]:
# TRAVEL_MISSION_CHECK의 첫번째 항목 가져오기
travel_list = []
for i in range(len(travel)):
    value = int(travel['TRAVEL_MISSION_CHECK'][i].split(';')[0])
    travel_list.append(value)

travel['TRAVEL_MISSION_PRIORITY'] = travel_list

### 변수 선택

TRAVEL_ID: 여행 ID

TRAVELER_ID: 여행자 ID

TRAVEL_MISSION_PRIORITY: 개별 미션 우선도 중 첫번째

In [15]:
travel = travel[['TRAVEL_ID', 'TRAVELER_ID', 'TRAVEL_MISSION_PRIORITY']]

## 3) traveller_master 여행자 정보 df

### 변수 선택

TRAVELER_ID 여행객ID

GENDER 성별

AGE_GRP 연령대

INCOME 소득

TRAVEL_STYL(1,2,3,4,5,6,7,8) 여행 스타일 

TRAVEL_MOVTIVE(1) 여행 동기 - 2,3은 결측치가 있어 제외

TRAVEL_NUM 여행빈도

TRAVEL_COMPANIONS_NUM 동반자 수


In [16]:
traveller_master = traveller_master[['TRAVELER_ID', 'GENDER', 'AGE_GRP', 'INCOME', 'TRAVEL_STYL_1', 
                                     'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4', 'TRAVEL_STYL_5', 
                                     'TRAVEL_STYL_6', 'TRAVEL_STYL_7','TRAVEL_STYL_8', 
                                      'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM' ]]

## 데이터 프레임 합치기

In [17]:
df = pd.merge(travel, traveller_master, left_on = 'TRAVELER_ID', right_on = 'TRAVELER_ID', how = 'inner')

In [18]:
df = pd.merge(visit_area_info, df, left_on = 'TRAVEL_ID', right_on = 'TRAVEL_ID', how = 'right')

## 만족도(y) 결측치 삭제

In [19]:
df = df.dropna(subset = ['DGSTFN'])
df.reset_index(drop=True, inplace=True)

## 체류시간 결측치 대체


체류시간 0을 median 60으로 바꾸기

In [20]:
df['RESIDENCE_TIME_MIN'] = df['RESIDENCE_TIME_MIN'].replace(0,60)

## 재방문여부 원핫인코딩

In [21]:
df['REVISIT_YN'] = df['REVISIT_YN'].replace("N",0)
df['REVISIT_YN'] = df['REVISIT_YN'].replace("Y",1)

## 여행스타일 결측치 삭제

In [22]:
df.dropna(subset = ['TRAVEL_STYL_1'], inplace = True)
df.reset_index(drop= True, inplace = True)

## 여행 목적 결측치 삭제

In [23]:
df.dropna(subset = ['TRAVEL_MOTIVE_1'], inplace = True)
df.reset_index(drop= True, inplace = True)

In [24]:
df.shape

(24102, 27)

In [25]:
df.isna().sum().sum()

0

# Train-test split

-유니크한 관광지 정보가 모두 train set에 있어야 한다. (train set에 경복궁 없고 test set에만 경복궁 있으면 안된다. 왜냐하면 방문지 변수가 있기 때문에 입력되지 않은 방문지에 대한 정보는 모델이 학습할 수 없기 때문이다.)

-또한 새로운 유저에 대한 추측이기 때문에 유저 데이터는 무조건 train / test 중 한 곳에만 있다. (유저 A의 ㄱ관광지는 train, ㄴ관광지는 test 에 있을 수 없다.)

-이를 반영해서 train test split 진행하면 된다. 

-train set에서만 (방문지마다 체류시간 평균, 추천의향의 평균, 재방문여부의 평균, 동반자 수의 평균, 재방문의향의 평균)을 산출하고, 이 값을 test set에 대입한다. 

In [26]:
df1 = df
Train = pd.DataFrame(columns = list(df.columns))
for i in tqdm(list(df['VISIT_AREA_NM'].unique())): # 유니크한 관광지 목록 중에서
    df2 = df1[df1['VISIT_AREA_NM'] == i] # 특정 관광지에 간 모든 사람 뽑아서
    np.random.seed(42)
    if df2.empty:
        pass
    else:
        random_number = np.random.randint(len(df2)) 
        df_id = df2.iloc[[random_number]] # 그 중 랜덤으로 관광지에 간 사람 한 명 뽑아서
        index = df_id.iloc[0,0]
        df3 = df1[df1['TRAVEL_ID'] == index] #그 사람이 간 모든 관광지를 구해서
        df1 = pd.merge(df3, df1, how = 'outer', indicator = True)
        df1 = df1.query('_merge =="right_only"').drop(columns = ['_merge']) # 기존 데이터프레임에서 그 사람 내용을 삭제하고
        Train = pd.concat([Train, df3], ignore_index=True) #train set 에 추가
'''        
이 프로세스를 반복하면 전체 데이터프레임(df)에 유저정보는 계속해서 삭제될 것이고, 남은 df가 test set,
Train 데이터프레임이 train set이 되는 것임
'''

100%|██████████| 6931/6931 [06:46<00:00, 17.06it/s]


'        \n이 프로세스를 반복하면 전체 데이터프레임(df)에 유저정보는 계속해서 삭제될 것이고, 남은 df가 test set,\nTrain 데이터프레임이 train set이 되는 것임\n'

In [27]:
while len(df1)/len(df) > 0.2:
    np.random.seed(42)
    random_number = np.random.randint(len(df1))
    df_id = df1.iloc[[random_number]]
    index = df_id.iloc[0,0]
    df3 = df1[df1['TRAVEL_ID'] == index]
    df1 = pd.merge(df3, df1, how = 'outer', indicator = True)
    df1 = df1.query('_merge =="right_only"').drop(columns = ['_merge'])
    Train = pd.concat([Train, df3], ignore_index=True)

In [28]:
print(len(Train)) # train set 길이
print(len(df1)) # test set 길이
print(len(df))
print(len(df1) / len(df))

19282
4820
24102
0.199983403866899


## Train set에서 방문지에 대한 변수 생성
방문지마다 체류시간 평균, 추천의향의 평균, 재방문여부의 평균, 동반자 수의 평균, 재방문의향의 평균 산출

In [29]:
#새로운 데이터프레임 생성해서, 이 데이터프레임에 평균값을 추가한 새로운 Train set 생성할 것임

new_train = pd.DataFrame(columns = list(Train.columns) + ['RESIDENCE_TIME_MIN_mean', 'RCMDTN_INTENTION_mean',
                                                          'REVISIT_YN_mean', 'TRAVEL_COMPANIONS_NUM_mean',
                                                          'REVISIT_INTENTION_mean'])


for i in tqdm(list(Train['VISIT_AREA_NM'].unique())): #유니크한 관광지 목록 중에서
    df2 = Train[Train['VISIT_AREA_NM'] == i] # 특정 관광지에 간 모든 사람 뽑아서
    for j in ['RESIDENCE_TIME_MIN', 'RCMDTN_INTENTION', 'REVISIT_YN', 'TRAVEL_COMPANIONS_NUM', 'REVISIT_INTENTION']:
        #체류시간 평균 산출 
        globals()[str(j)+'_mean'] = df2[str(j)]
        globals()[str(j)+'_mean'] = np.mean(globals()[str(j)+'_mean'])
        #데이터프레임에 들어가게 값을 리스트 형태로 변환
        globals()[str(j)+'_mean'] = np.repeat(globals()[str(j)+'_mean'], len(df2)) 
        df2[str(j)+'_mean'] = globals()[str(j)+'_mean']
    #새로운 데이터프레임에 방문지별 평균값 대입
    new_train = pd.concat([new_train, df2], axis = 0)

100%|██████████| 6931/6931 [01:00<00:00, 115.19it/s]


In [30]:
#편의를 위해 유저별 정렬
new_train.sort_values(by = ['TRAVEL_ID'], axis = 0, inplace = True)

## DATA SET 저장

In [31]:
#train set 저장
new_train.to_csv(path + '/Trainset.csv', index = False)
#test set 저장
df1.to_csv(path + '/Testset.csv', index = False)

In [32]:
# 파일 불러오기
Train = pd.read_csv(path + '/Trainset.csv')
test = pd.read_csv(path + '/Testset.csv')

In [33]:
Train.dropna(inplace = True)
Train.reset_index(inplace = True, drop = True )

In [34]:
test.dropna(inplace = True)
test.reset_index(inplace = True, drop = True )

In [35]:
print(Train.shape)
print(test.shape)

(19282, 32)
(4820, 27)


# Train set 여행 방문지 필터링

## 5번 이상 방문한 곳에 대해서만 학습 / 테스트

In [36]:
count = pd.DataFrame(Train['VISIT_AREA_NM'].value_counts())

In [37]:
print(count)

               count
VISIT_AREA_NM       
함덕해수욕장           135
첨성대              116
협재해수욕장           112
성산일출봉            110
광안리해수욕장          100
...              ...
월정교,첨성대            1
경주세계문화엑스포재단        1
부산항 제1부두           1
드림센터               1
남제주 비행기 격납고        1

[6931 rows x 1 columns]


In [38]:
Train.reset_index(drop = True, inplace= True)
#5번 이상 방문한 곳으로만 필터링
count = pd.DataFrame(Train['VISIT_AREA_NM'].value_counts())
count['places'] = count.index

In [39]:
### 여기 숫자 변경
five_places = list(count[count['count']>=3]['places'])
###
for i in range(len(Train)):
    if Train['VISIT_AREA_NM'][i] not in five_places:
        Train = Train.drop([i], axis = 0)
Train.reset_index(drop = True, inplace = True)

In [40]:
#확인
count1 = pd.DataFrame(Train['VISIT_AREA_NM'].value_counts())
print(count1)

               count
VISIT_AREA_NM       
함덕해수욕장           135
첨성대              116
협재해수욕장           112
성산일출봉            110
광안리해수욕장          100
...              ...
나정고운모래해변           3
동화사                3
대청댐전망대             3
어은돌해수욕장            3
아끈다랑쉬오름            3

[1571 rows x 1 columns]


In [41]:
Train.shape

(12893, 32)

In [42]:
print(Train.shape)
print(test.shape)

(12893, 32)
(4820, 27)


# Catboost 모델 기반 추천시스템 학습

In [43]:
#학습에 필요없는 feature 제거
Train.drop(['TRAVELER_ID', 'REVISIT_INTENTION',
            'RCMDTN_INTENTION','RESIDENCE_TIME_MIN', 'REVISIT_YN'], axis = 1, inplace = True)
test.drop(['TRAVELER_ID', 'REVISIT_INTENTION',
            'RCMDTN_INTENTION','RESIDENCE_TIME_MIN', 'REVISIT_YN'], axis = 1, inplace = True)

In [44]:
# 데이터 타입 변경
Train['VISIT_AREA_TYPE_CD'] = Train['VISIT_AREA_TYPE_CD'].astype('string')
test['VISIT_AREA_TYPE_CD'] = test['VISIT_AREA_TYPE_CD'].astype('string')
Train['VISIT_AREA_ID'] = Train['VISIT_AREA_ID'].astype('string')
test['VISIT_AREA_ID'] = test['VISIT_AREA_ID'].astype('string')


In [45]:
y_train = Train['DGSTFN']
X_train = Train.drop(['DGSTFN'], axis = 1)

## 초모수 조절
Cross Validation Set 생성 + Random Search 함수

train set의 feature, target, cv 개수를 입력하면 cross validaiton set을 생성해주는 함수 생성

최대한 많은 관광지 정보를 보존하기 위해 cv = 10 으로 설정

In [46]:
def cross_validation(X_train, y_train, cv, iteration,number, random_state): #X_train 데이터, y_train 데이터, cv 개수, random search 횟수, random_state

    X_train1 = X_train #변수 옮기기
    y_train1 = y_train #변수 옮기기
    for i in range(cv): #각 fold마다의 X_train, y_train 생성 (Train_1, Train_2, ... / target_1, target_2, ...)
        globals()['Train_'+str(i+1)] = pd.DataFrame(columns = list(X_train.columns))
        globals()['target_'+str(i+1)] = []
    print(str(cv)+'개의 fold를 생성중입니다.....')
    for i in tqdm(range(cv)):
        np.random.seed(random_state) #초기 시드 설정
        while (len(globals()['Train_'+str(i+1)]) / len(X_train)) < (1/cv): #1/cv 비율 만큼의 데이터가 모일 때까지
            random_number = np.random.randint(len(X_train1))
            df_id = X_train1.iloc[[random_number]]
            index = df_id.iloc[0,0] #랜덤하게 유저를 선택하고
            df1 = X_train1[X_train1['TRAVEL_ID'] == index] #그 유저가 갔던 모든 여행지 불러오고
            target_index = X_train1[X_train1['TRAVEL_ID'] == index].index
            X_train1 = pd.merge(df1, X_train1, how = 'outer', indicator = True)
            X_train1 = X_train1.query('_merge =="right_only"').drop(columns = ['_merge']) #기존 데이터프레임은 해당 유저 정보 삭제
            globals()['Train_'+str(i+1)] = pd.concat([globals()['Train_'+str(i+1)], df1], ignore_index=True) #validation set에 유저의 X_train 삽입
            globals()['target_'+str(i+1)].extend(list(y_train[list(target_index)])) #유저의 X_train에 상응하는 y_train 삽입
            if len(X_train1) == 0: #기존 데이터프레임에 모든 유저정보가 사라지면 validation set 생성이 완료된 것이므로 정지
                break
    print(str(cv)+'개의 fold 생성이 완료되었습니다!')
    print('함수에서 설정한 초모수 범위 내에서 ' + str(cv)+'개의 validation 검정을 진행합니다...' )
    
    
    np.random.seed(random_state)
    initial = 0 
    for a in tqdm(range(iteration)):
        print(str(a+1) + "번째 초모수 조절치에 대한 학습을 진행합니다....")
        ##########여기에 원하는 hyperparameter 기입###########
        ######################################################
        n_estimators = np.random.choice(np.arange(700, 1301, 50))
        max_depth = np.random.choice(np.arange(5, 11, 1))
        subsample = np.random.choice(np.arange(0.75, 1.0001, 0.05))
        colsample_bylevel = np.random.choice(np.arange(0.8, 1.0001, 0.05))
        ######################################################
######################################################
        final_recall = [] # K개의 검증 성능이 들어갈 리스트

        for j in range(cv): #K개 fold중
            print(str(a+1) + '번째 초모수 조절치의' + str(j+1)+'번째 fold를 학습하고 있습니다....')
            #한 fold에 대해서 학습
            combine_df_list = list(range(1, (cv+1))) # 1부터 cv까지 숫자리스트 만들어서
            del combine_df_list[j] #숫자 하나를 지우고, 그 숫자가 있는 Train set을 Validation set으로 설정
            #예를 들어 1이 빠졌으면 Train_1이 validation set, Train_2, Train_3, ... 는 Train set
            X_new_train = pd.DataFrame(columns = list(globals()['Train_'+str(j+1)].columns))
            y_new_train = []
            for i in combine_df_list: #지운 숫자 외의 숫자가 있는 Train set들을 결합
                X_new_train = pd.concat([X_new_train, globals()['Train_'+str(i)]], axis = 0) #X_train 결합
                y_new_train.extend(globals()['target_'+str(i)]) #y_train 결합
            y_new_train = np.array(y_new_train).astype(float)
            X_new_train.drop(['TRAVEL_ID'], axis = 1, inplace = True) #필요 없는 컬럼 제거
            if 'DGSTFN' in list(X_new_train.columns): #global 함수에서 발생하는 오류 해결
                X_new_train.drop(['DGSTFN'], axis = 1, inplace = True)
            model = CatBoostRegressor(n_estimators = n_estimators,
                                  max_depth = max_depth,
                                  subsample = subsample,
                                  colsample_bylevel = colsample_bylevel,
                                  cat_features = ['VISIT_AREA_NM', 'SIDO', 'GUNGU','VISIT_AREA_TYPE_CD', 'VISIT_AREA_ID',
                                              'TRAVEL_MISSION_PRIORITY', 'AGE_GRP', 'GENDER'], 
                                  random_state = 42)
        ##############################################################################################

            model.fit(X_new_train, y_new_train) #########모델 적합

            #학습한 fold에 대한 test 값 도출
            recall_10_list = [] #validation set의 recall 측정값들이 들어갈 리스트
            #####################유저 정보##################################
            data = globals()['Train_'+str(j+1)][['TRAVEL_ID', 'SIDO', 'GUNGU', 'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                                    'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                                    'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                                    'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM']]
            data1 = pd.DataFrame(columns=['TRAVEL_ID', 'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                                    'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                                    'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                                    'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM', 'sido_gungu_list'])
            for i in list(data['TRAVEL_ID'].unique()):
                temp_df = data[data['TRAVEL_ID'] == i]
                temp_df1 = temp_df[['SIDO', 'GUNGU']] #각 유저별 방문한 시군구 확인
                temp_df1.reset_index(drop = True, inplace = True)
                sido_gungu_visit = []
                for k in range(len(temp_df1)):
                    sido_gungu_visit.append(temp_df1['SIDO'][k] + '+' + temp_df1['GUNGU'][k])
                sido_gungu_list = list(set(sido_gungu_visit))
                new = temp_df.drop(['SIDO', 'GUNGU'], axis = 1) #기존 시도, 군구 제외하고
                new = new.head(1)
                new['sido_gungu_list'] = str(sido_gungu_list)
                data1 = pd.concat([data1, new], axis = 0) #새로운 데이터프레임 생성 
            data1.reset_index(drop = True, inplace = True)
            ##########################여행지 정보################################
            info = X_new_train[['SIDO', 'VISIT_AREA_NM', 'GUNGU','VISIT_AREA_TYPE_CD','VISIT_AREA_ID', 'RESIDENCE_TIME_MIN_mean', 'RCMDTN_INTENTION_mean',
            'REVISIT_YN_mean', 'TRAVEL_COMPANIONS_NUM_mean', 'REVISIT_INTENTION_mean']]
            info.drop_duplicates(['VISIT_AREA_NM'], inplace = True)
            ###### 2회 이상 관광한 방문지 리스트 생성
            visiting_list = X_new_train[['VISIT_AREA_NM']] #train set에 있는 방문지에 대해서만 2회 이상 방문하였는지 확인
            visiting_list.reset_index(drop = True, inplace = True)
            #데이터 전처리
            dfdf = pd.DataFrame(visiting_list.value_counts(), columns = ['count'])
            dfdf['VISIT_AREA_NM'] = dfdf.index
            dfdf.reset_index(drop = True, inplace = True)
            for i in range(len(dfdf)):
                dfdf['VISIT_AREA_NM'][i] = str(dfdf['VISIT_AREA_NM'][i])
                dfdf['VISIT_AREA_NM'][i] = dfdf['VISIT_AREA_NM'][i].replace("(","").replace(")","").replace(",","").replace("\''","")
                dfdf['VISIT_AREA_NM'][i] = dfdf['VISIT_AREA_NM'][i][1:-1]
            #n회 이상 적용
            dfdf = dfdf[dfdf['count'] >= number] 
            visit_list = list(dfdf['VISIT_AREA_NM']) #visit_list에 2회 이상 방문지 리스트
            #방문지가 2회 이상 방문한 관광지 아니면 제거
            info.reset_index(drop = True, inplace = True)
            for i in range(len(info)):
                if info['VISIT_AREA_NM'][i] not in visit_list:
                    info = info.drop([i], axis = 0)
            info.reset_index(drop = True, inplace = True)
            ##########################모델 10개 관광지 추천############################
            result = []
            for i in range(len(data1)):
                #데이터

                final_df = pd.DataFrame(columns = ['VISIT_AREA_NM', 'SIDO', 'GUNGU', 'VISIT_AREA_TYPE_CD', 'VISIT_AREA_ID',
                       'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                       'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                       'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                       'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM',
                       'RESIDENCE_TIME_MIN_mean', 'RCMDTN_INTENTION_mean', 'REVISIT_YN_mean',
                       'TRAVEL_COMPANIONS_NUM_mean', 'REVISIT_INTENTION_mean']) #빈 데이터프레임에 내용 추가
                ####### 시/도 군/구 별 자료 수집
                temp = data1['sido_gungu_list'][i].replace("[","").replace("]","").replace("\'","").replace(", ",",")
                places_list = list(map(str, temp.split(",")))
                for q in places_list:
                    sido, gungu = map(str, q.split("+"))

                    info_df = info[(info['SIDO'] == sido) & (info['GUNGU'] == gungu)] 

                    info_df.drop(['SIDO'], inplace = True, axis = 1)
                    info_df.reset_index(inplace = True, drop = True)
                    data2 = data1.drop(['sido_gungu_list'], axis =1)
                    user_df = pd.DataFrame([data2.iloc[i].to_list()]*len(info_df), columns = ['SIDO', 'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                                        'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                                        'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                                        'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM'])
                    df = pd.concat([user_df, info_df], axis = 1)
                    df = df[['VISIT_AREA_NM', 'SIDO', 'GUNGU', 'VISIT_AREA_TYPE_CD', 'VISIT_AREA_ID',
                   'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                   'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                   'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                   'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM',
                   'RESIDENCE_TIME_MIN_mean', 'RCMDTN_INTENTION_mean', 'REVISIT_YN_mean',
                   'TRAVEL_COMPANIONS_NUM_mean', 'REVISIT_INTENTION_mean']] # 변수정렬
                    df['VISIT_AREA_TYPE_CD'] = df['VISIT_AREA_TYPE_CD'].astype('string')
                    final_df = pd.concat([final_df, df], axis = 0)
                final_df.reset_index(drop = True, inplace = True)
                final_df.drop_duplicates(['VISIT_AREA_NM'], inplace = True)

                #모델 예측
                y_pred = model.predict(final_df)
                y_pred = pd.DataFrame(y_pred, columns = ['y_pred'])
                test_df1 = pd.concat([final_df, y_pred], axis = 1)
                test_df1.sort_values(by = ['y_pred'], axis = 0, ascending=False, inplace = True) # 예측치가 높은 순대로 정렬

                test_df1 = test_df1.iloc[0:10,] #상위 10개 관광지 추천

                visiting_candidates = list(test_df1['VISIT_AREA_NM']) # 모델이 추천한 관광지들을 리스트 형태로 변환

               # 유저정보와 추천 관광지
                test_df2 = test_df1[['SIDO','TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                                    'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                                    'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                                    'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM']]
                if len(test_df2) == 0:
                    rec = []
                    result.append(rec)
                else:

                    rec = test_df2.iloc[0].to_list()

                    rec.append(visiting_candidates)

                    result.append(rec)
            final_df = pd.DataFrame(result,
                                columns = ['SIDO', 'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                                'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                                'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                                'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM', 'recommend_result_place'])
            final_df = final_df[['recommend_result_place']]
            travel_id = data1[['TRAVEL_ID']]
            travel_id.reset_index(drop = True, inplace = True)
            final_df = pd.concat([travel_id, final_df], axis = 1)

            #추천지 10개 미만인 여행 ID확인
            travel_id_list = []
            for i in range(len(final_df)):
                recommend_list = final_df['recommend_result_place'][i]
                if str(recommend_list).count(',') < 9:
                    travel_id_list.append(final_df['TRAVEL_ID'][i])
                if pd.isna(str(recommend_list)):
                    travel_id_list.append(final_df['TRAVEL_ID'][i])
            ## 군구 리스트
            places = list(set(globals()['Train_'+str(j+1)]['GUNGU']))
            for i in range(len(places)):
                if places[i][-1] == '구' or places[i][-1] == '시' or places[i][-1] == '군':
                    places[i] = places[i][:-1]

            ###############################################################
            ######## 최종 성능 평가 #########################################
            #########################################################
            visit_list = list(info['VISIT_AREA_NM'])
            globals()['Train_'+str(j+1)]['DGSTFN'] = globals()['target_'+str(j+1)]



            for i in list(globals()['Train_'+str(j+1)]['TRAVEL_ID'].unique()):

                #추천한 방문지가 10개 미만이면 0
                if i in travel_id_list:
                    recall_10_list.append(0)
                    continue

                satisfied = globals()['Train_'+str(j+1)][globals()['Train_'+str(j+1)]['TRAVEL_ID'] == i] #실제(y_actual) 관광객이 만족한 관광지
                satisfied.reset_index(drop = True, inplace = True) 


                satisfied1 = satisfied[satisfied['DGSTFN'] >=4 ] #만족의 기준은 4이상 일때만 만족이라고 정의
                if len(satisfied1) == 0: # 유저가 만족한 관광지가 하나도 없으면 recall@10은 어차피 0
                    recall_10_list.append(0)
                    continue
                else:
                    item_list = satisfied1['VISIT_AREA_NM']


                item_list = list(set(item_list))


            #final_df의 추천지 10개랑 비교

                recommend_list = final_df[final_df['TRAVEL_ID'] == i]['recommend_result_place'] #모델 추천 관광지 30개

                summ = 0
                for n in item_list:
                    word_list = list(n.split(' '))
                    if word_list[-1][-1] == '점': #지점명 삭제
                        del word_list[-1]
                    for o in word_list:
                        if o in places:#장소에 군/구 명 있으면 아무것도 하지 않고 스킵
                            pass
                        else:
                            for p in recommend_list: #장소에 교차어 있으면 해당 장소는 방문했다고 인식하기
                                if o in str(p) :
                                    summ += 1
                recall10_for_1user = summ / min(10, len(satisfied1)) #recall@10 산식
                if recall10_for_1user > 1:
                    recall10_for_1user = 1
                recall_10_list.append(recall10_for_1user)
            globals()['Train_'+str(j+1)].drop(['DGSTFN'], axis = 1, inplace = True) #globals 함수 오류 해결하기 위한 코드
            
            recall_for_one_cv = sum(recall_10_list) / len(recall_10_list) #한 fold에 대한 recall@10값 추출
                
            final_recall.append(recall_for_one_cv)

        recallat10 = sum(final_recall) / len(final_recall)
        print('이번 결과는:', recallat10)
        ###################### hyperparameter 바꾸면 여기도 수정해야 ######################
        ###################################################################################
        print('이번 결과의 parameter은: ', 'n_estimators:', n_estimators, 'max_depth:', max_depth, 
                  'subsample:', subsample, 'colsample_bylevel:', colsample_bylevel)
        if recallat10 > initial:
            initial = recallat10
            print('신기록!:', initial)
            print('n_estimators:', n_estimators, 'max_depth:', max_depth, 
                  'subsample:', subsample, 'colsample_bylevel:', colsample_bylevel)
            final_estimator = n_estimators
            final_max_depth = max_depth
            final_subsample = subsample
            final_colsample_bylevel = colsample_bylevel
         #####################################################################################
    print('최종 parameter은 :',  final_estimator, 'max_depth:', final_max_depth, 
                  'subsample:', final_subsample, 'colsample_bylevel:', final_colsample_bylevel)
    return(initial)

In [47]:
#초모수 조절
cross_validation(X_train, y_train, cv = 10, iteration = 10, number = 2, random_state = 42)

10개의 fold를 생성중입니다.....


100%|██████████| 10/10 [03:53<00:00, 23.33s/it]


10개의 fold 생성이 완료되었습니다!
함수에서 설정한 초모수 범위 내에서 10개의 validation 검정을 진행합니다...


  0%|          | 0/10 [00:00<?, ?it/s]

1번째 초모수 조절치에 대한 학습을 진행합니다....
1번째 초모수 조절치의1번째 fold를 학습하고 있습니다....
Learning rate set to 0.060307
0:	learn: 0.7723666	total: 91.2ms	remaining: 1m 31s
1:	learn: 0.7722823	total: 96.8ms	remaining: 48.3s
2:	learn: 0.7716805	total: 111ms	remaining: 36.9s
3:	learn: 0.7712912	total: 127ms	remaining: 31.7s
4:	learn: 0.7708924	total: 144ms	remaining: 28.7s
5:	learn: 0.7707026	total: 158ms	remaining: 26.1s
6:	learn: 0.7704760	total: 172ms	remaining: 24.4s
7:	learn: 0.7700950	total: 188ms	remaining: 23.4s
8:	learn: 0.7695462	total: 204ms	remaining: 22.5s
9:	learn: 0.7692100	total: 217ms	remaining: 21.5s
10:	learn: 0.7690705	total: 231ms	remaining: 20.8s
11:	learn: 0.7686269	total: 244ms	remaining: 20.1s
12:	learn: 0.7683373	total: 260ms	remaining: 19.7s
13:	learn: 0.7679678	total: 275ms	remaining: 19.4s
14:	learn: 0.7677188	total: 288ms	remaining: 18.9s
15:	learn: 0.7673451	total: 302ms	remaining: 18.6s
16:	learn: 0.7669403	total: 315ms	remaining: 18.2s
17:	learn: 0.7666161	total: 331ms	remaining:

...

No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded


10번째 초모수 조절치의10번째 fold를 학습하고 있습니다....
Learning rate set to 0.050317
0:	learn: 0.7744633	total: 15.2ms	remaining: 18.9s
1:	learn: 0.7740782	total: 26.8ms	remaining: 16.7s
2:	learn: 0.7736718	total: 39ms	remaining: 16.2s
3:	learn: 0.7730637	total: 51.7ms	remaining: 16.1s
4:	learn: 0.7728933	total: 65.9ms	remaining: 16.4s
5:	learn: 0.7727930	total: 76.8ms	remaining: 15.9s
6:	learn: 0.7723353	total: 89.5ms	remaining: 15.9s
7:	learn: 0.7719204	total: 100ms	remaining: 15.5s
8:	learn: 0.7715353	total: 114ms	remaining: 15.7s
9:	learn: 0.7714686	total: 116ms	remaining: 14.4s
10:	learn: 0.7712618	total: 128ms	remaining: 14.4s
11:	learn: 0.7709417	total: 139ms	remaining: 14.4s
12:	learn: 0.7705991	total: 153ms	remaining: 14.6s
13:	learn: 0.7702632	total: 168ms	remaining: 14.8s
14:	learn: 0.7700371	total: 182ms	remaining: 15s
15:	learn: 0.7696429	total: 195ms	remaining: 15.1s
16:	learn: 0.7691569	total: 209ms	remaining: 15.1s
17:	learn: 0.7687791	total: 221ms	remaining: 15.1s
18:	learn: 0.7684944	

No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
100%|██████████| 10/10 [58:20<00:00, 350.00s/it]

이번 결과는: 0.25686807613748003
이번 결과의 parameter은:  n_estimators: 1250 max_depth: 8 subsample: 0.75 colsample_bylevel: 0.9000000000000001
신기록!: 0.25686807613748003
n_estimators: 1250 max_depth: 8 subsample: 0.75 colsample_bylevel: 0.9000000000000001
최종 parameter은 : 1250 max_depth: 8 subsample: 0.75 colsample_bylevel: 0.9000000000000001


0.25686807613748003

## Catboost 적합

범주형 변수 목록

VISIT_AREA_NM 방문지

SIDO 시도

GUNGU 군구

VISIT_AREA_CD 관광지 종류 코드

TRAVEL_MISSION_PRIORITY 유저가 설정한 본인의 미션 중 첫번째

AGE_GRP 연령대

GENDER 성별

In [48]:
y_train = Train['DGSTFN']
X_train = Train.drop(['DGSTFN', 'TRAVEL_ID'], axis = 1)

In [49]:
model = CatBoostRegressor(n_estimators = 1150, max_depth = 10, subsample = 0.9500000000000002, 
                          colsample_bylevel = 0.9500000000000002,
    cat_features = ['VISIT_AREA_NM', 'SIDO', 'GUNGU','VISIT_AREA_TYPE_CD',
                                                  'TRAVEL_MISSION_PRIORITY', 'AGE_GRP', 'GENDER'], random_state = 42)
model.fit(X_train, y_train)

Learning rate set to 0.054735
0:	learn: 0.7834265	total: 15.7ms	remaining: 18s
1:	learn: 0.7789890	total: 33.8ms	remaining: 19.4s
2:	learn: 0.7757984	total: 38.3ms	remaining: 14.6s
3:	learn: 0.7720146	total: 54.6ms	remaining: 15.6s
4:	learn: 0.7688662	total: 59.1ms	remaining: 13.5s
5:	learn: 0.7651642	total: 76.3ms	remaining: 14.5s
6:	learn: 0.7620738	total: 93.5ms	remaining: 15.3s
7:	learn: 0.7592788	total: 109ms	remaining: 15.6s
8:	learn: 0.7565778	total: 124ms	remaining: 15.7s
9:	learn: 0.7543687	total: 141ms	remaining: 16.1s
10:	learn: 0.7519043	total: 161ms	remaining: 16.6s
11:	learn: 0.7501449	total: 167ms	remaining: 15.9s
12:	learn: 0.7491678	total: 169ms	remaining: 14.8s
13:	learn: 0.7477594	total: 172ms	remaining: 14s
14:	learn: 0.7457257	total: 193ms	remaining: 14.6s
15:	learn: 0.7437224	total: 216ms	remaining: 15.3s
16:	learn: 0.7420257	total: 238ms	remaining: 15.9s
17:	learn: 0.7404024	total: 258ms	remaining: 16.3s
18:	learn: 0.7390792	total: 278ms	remaining: 16.6s
19:	lear

In [50]:
joblib.dump(model,path + '/travel_recommend_model.pkl')

['/Users/takhaseon/Documents/KTB/project/TripPop/data/travel_recommend_model.pkl']

In [53]:
model = joblib.load(path + '/travel_recommend_model.pkl')
test = pd.read_csv(path + '/Testset.csv')
train = pd.read_csv(path + '/Trainset.csv')

# Test B

## 모델의 10개 관광지 후보 불러오기

### 유저 정보

In [54]:
y_test = test['DGSTFN']
X_test = test.drop(['DGSTFN'], axis = 1)

In [55]:
#유저정보
data = test[['TRAVEL_ID', 'SIDO', 'GUNGU', 'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                            'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                            'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                            'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM']]

In [56]:
#내가 간 시도 군구 리스트:
data1 = pd.DataFrame(columns=['TRAVEL_ID', 'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                            'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                            'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                            'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM', 'sido_gungu_list'])
for i in tqdm(list(data['TRAVEL_ID'].unique())):
    temp_df = data[data['TRAVEL_ID'] == i]
    temp_df1 = temp_df[['SIDO', 'GUNGU']] #각 유저별 방문한 시군구 확인
    temp_df1.reset_index(drop = True, inplace = True)
    sido_gungu_visit = []
    for j in range(len(temp_df1)):
        sido_gungu_visit.append(temp_df1['SIDO'][j] + '+' + temp_df1['GUNGU'][j])
    sido_gungu_list = list(set(sido_gungu_visit))
    new = temp_df.drop(['SIDO', 'GUNGU'], axis = 1) #기존 시도, 군구 제외하고
    new = new.head(1)
    new['sido_gungu_list'] = str(sido_gungu_list)
    data1 = pd.concat([data1, new], axis = 0) #새로운 데이터프레임 생성        
    

100%|██████████| 2110/2110 [00:08<00:00, 239.05it/s]


In [57]:
#유저 정보 저장
data1.reset_index(drop = True, inplace = True)
data1.to_csv(path + '/Testset_user_info.csv', index=False)

### 여행지 정보

In [58]:
#여행지 정보
info = train[['SIDO', 'VISIT_AREA_NM', 'GUNGU','VISIT_AREA_TYPE_CD','VISIT_AREA_ID','RESIDENCE_TIME_MIN_mean', 'RCMDTN_INTENTION_mean',
            'REVISIT_YN_mean', 'TRAVEL_COMPANIONS_NUM_mean', 'REVISIT_INTENTION_mean']]
info.drop_duplicates(['VISIT_AREA_NM'], inplace = True)

2회 이상 방문지 리스트 뽑아서 여행지 정보에 없는 것 제거

In [59]:
###### 2회 이상 관광한 방문지 리스트 생성
visiting_list = train[['VISIT_AREA_NM']] #train set에 있는 방문지에 대해서만 2회 이상 방문하였는지 확인
visiting_list.reset_index(drop = True, inplace = True)
#데이터 전처리
dfdf = pd.DataFrame(visiting_list.value_counts(), columns = ['count'])
dfdf['VISIT_AREA_NM'] = dfdf.index
dfdf.reset_index(drop = True, inplace = True)
for i in range(len(dfdf)):
    dfdf['VISIT_AREA_NM'][i] = str(dfdf['VISIT_AREA_NM'][i])
    dfdf['VISIT_AREA_NM'][i] = dfdf['VISIT_AREA_NM'][i].replace("(","").replace(")","").replace(",","").replace("\''","")
    dfdf['VISIT_AREA_NM'][i] = dfdf['VISIT_AREA_NM'][i][1:-1]
#5회 이상 적용
dfdf = dfdf[dfdf['count'] >= 2]
visit_list = list(dfdf['VISIT_AREA_NM']) #visit_list에 5회 이상 방문지 리스트

In [60]:
#방문지가 5회 이상 방문한 관광지 아니면 제거
info.reset_index(drop = True, inplace = True)
for i in tqdm(range(len(info))):
    if info['VISIT_AREA_NM'][i] not in visit_list:
        info = info.drop([i], axis = 0)
info.reset_index(drop = True, inplace = True)

100%|██████████| 6931/6931 [00:04<00:00, 1606.17it/s]


In [61]:
#여행자 정보 저장
info.reset_index(drop = True, inplace = True)
info.to_csv(path + '/Testset_travel_info.csv', index=False)

### 모델의 10개 추천 관광지 목록 제작 코드

In [62]:
data = pd.read_csv(path + '/Testset_user_info.csv')
info = pd.read_csv(path + '/Testset_travel_info.csv')

In [63]:
result = []
for i in tqdm(range(len(data1))):
    #데이터
    
    final_df = pd.DataFrame(columns = ['VISIT_AREA_NM', 'SIDO', 'GUNGU', 'VISIT_AREA_TYPE_CD', 'VISIT_AREA_ID',
           'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
           'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
           'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
           'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM',
           'RESIDENCE_TIME_MIN_mean', 'RCMDTN_INTENTION_mean', 'REVISIT_YN_mean',
           'TRAVEL_COMPANIONS_NUM_mean', 'REVISIT_INTENTION_mean']) #빈 데이터프레임에 내용 추가
    ####### 시/도 군/구 별 자료 수집
    temp = data1['sido_gungu_list'][i].replace("[","").replace("]","").replace("\'","").replace(", ",",")
    places_list = list(map(str, temp.split(",")))
    for q in places_list:
        sido, gungu = map(str, q.split("+"))

        info_df = info[(info['SIDO'] == sido) & (info['GUNGU'] == gungu)]

        info_df.drop(['SIDO'], inplace = True, axis = 1)
        info_df.reset_index(inplace = True, drop = True)
        data2 = data1.drop(['sido_gungu_list'], axis =1)
        user_df = pd.DataFrame([data2.iloc[i].to_list()]*len(info_df), columns = ['SIDO', 'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                            'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                            'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                            'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM'])
        df = pd.concat([user_df, info_df], axis = 1)
        df = df[['VISIT_AREA_NM', 'SIDO', 'GUNGU', 'VISIT_AREA_TYPE_CD', 'VISIT_AREA_ID',
       'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
       'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
       'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
       'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM',
       'RESIDENCE_TIME_MIN_mean', 'RCMDTN_INTENTION_mean', 'REVISIT_YN_mean',
       'TRAVEL_COMPANIONS_NUM_mean', 'REVISIT_INTENTION_mean']] # 변수정렬
        df['VISIT_AREA_TYPE_CD'] = df['VISIT_AREA_TYPE_CD'].astype('string')
        final_df = pd.concat([final_df, df], axis = 0)
    final_df.reset_index(drop = True, inplace = True)
    final_df.drop_duplicates(['VISIT_AREA_NM'], inplace = True)

    #모델 예측
    y_pred = model.predict(final_df)
    y_pred = pd.DataFrame(y_pred, columns = ['y_pred'])
    test_df1 = pd.concat([final_df, y_pred], axis = 1)
    test_df1.sort_values(by = ['y_pred'], axis = 0, ascending=False, inplace = True) # 예측치가 높은 순대로 정렬

    test_df1 = test_df1.iloc[0:10,] #상위 10개 관광지 추천

    visiting_candidates = list(test_df1['VISIT_AREA_NM']) # 모델이 추천한 관광지들을 리스트 형태로 변환

# 유저정보와 추천 관광지
    test_df2 = test_df1[['SIDO','TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                        'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                        'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                        'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM']]
    if len(test_df2) == 0:
        rec = []
        result.append(rec)
    else:
        
        rec = test_df2.iloc[0].to_list()

        rec.append(visiting_candidates)

        result.append(rec)



100%|██████████| 2110/2110 [00:40<00:00, 52.07it/s]


In [64]:
final_df = pd.DataFrame(result,
                            columns = ['SIDO', 'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                            'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                            'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                            'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM', 'recommend_result_place'])
final_df = final_df[['recommend_result_place']]
travel_id = data1[['TRAVEL_ID']]
travel_id.reset_index(drop = True, inplace = True)
final_df = pd.concat([travel_id, final_df], axis = 1)

In [65]:
#output_df 저장
final_df.to_csv(path + '/Testset_OUTPUT.csv', index=False)
#output_df 불러오기
final_df = pd.read_csv(path + '/Testset_OUTPUT.csv')

## 실제 유저가 다녀온 관광지랑 비교하여 Recall@10 산출

In [66]:
final_df

TRAVEL_ID                             recommend_result_place
0     a_a006728  ['임진각관광지', '마장호수', '헤이리무장애노을숲길', '파주출판도시', '잇츠...
1     a_a010544  ['킨텍스 제2전시장', '정발산', '고양어린이박물관', '중남미문화원', '일산...
2     a_a001405  ['국립유명산자연휴양림', '경반계곡', '경강교 인증센터', '용추폭포', '아침...
3     a_a005503  ['메가박스 성수', '그라운드시소 성수', '서울숲', '아더 스페이스 2.0 플...
4     a_a001129  ['백범광장', '충무아트센터 대극장', '국립현대미술관 덕수궁관', '덕수궁', ...
...         ...                                                ...
2105  d_d005323  ['김녕해안도로', '종달리해변', '금악성당', '삼무공원', '안돌오름', '성...
2106  d_d012354  ['김녕해안도로', '김녕성세기해변 인증센터', '삼무공원', '도두항', '금악성...
2107  d_d000293  ['취다선 티앤메디테이션', '영락리 방파제', '도두항', '철새 천연기념물 희귀...
2108  d_d006120  ['법화사', '서광동리곶자왈생태탐방로', '졸띠체험승마', '붉은오름자연휴양림',...
2109  d_d000483  ['도두항', '철새 천연기념물 희귀새도래및철새서식지', '서광동리곶자왈생태탐방로'...

[2110 rows x 2 columns]

In [67]:
#추천지 10개 미만인 여행 ID확인
travel_id_list = []
for i in tqdm(range(len(final_df))):
    recommend_list = final_df['recommend_result_place'][i]
    if pd.isna(recommend_list):
        travel_id_list.append(final_df['TRAVEL_ID'][i])
        continue
    if recommend_list.count(',') < 9:
        travel_id_list.append(final_df['TRAVEL_ID'][i])

100%|██████████| 2110/2110 [00:00<00:00, 72220.57it/s]


In [68]:
#군/군 리스트 출력
## 이 부분 해결 하기 위해서 군/구 목록 places라는 변수에 뽑아오기
'''
4. 성능을 올리기 위해 다음과 같은 추가 방법 도입:
- 아무래도 사람이 수기로 데이터를 입력하다 보니까 유사/동일 장소를 갔음에도 컴퓨터는 다른 장소로 인식 
    -ex1: ’파라다이스시티‘와 ’파라다이스시티 주차장‘을 다른 장소로 인식
    -ex2: ‘국립중앙박물관 특별전시관’과 ‘국립중앙박물관’을 다른 장소로 인식
- 그러므로 ‘모델이 추천한 추천지 10개’와 ‘유저가 만족한다고 했던 곳’을 단어 별로 쪼개서 공통어가 있으면 교집합 개수에 추가
    -ex1: ‘파라다이스시티’와 ‘파라다이스시티 주차장’은 ‘파라다이스시티’라는 공통어가 있으므로 교집합 개수에 추가
    -ex2: ‘국립중앙박물관 특별전시관’과 ‘국립중앙박물관’은 ‘국립중앙박물관’이라는 공통어가 있으므로 교집합 개수에 추가
- ‘파주점’, ‘하남점’ 등 지점명이 공통어가 되는 경우 배제
    -ex1: ‘롯데프리미엄아울렛 파주점'이라는 장소가 있을 때, 마지막 단어의 마지막 글자가 '점'일 경우에 마지막 글자를 제거 (공통어 비교 시 '롯데프리미엄아울렛'만 비교)
- 유저가 방문한 장소에 군/구가 공통어가 되는 경우 배제
    -ex1: 유저가 방문한 '스타필드 고양'은 ’스타필드‘, ’고양‘으로 나누어지는데, '고양'이라는 군/구 명을 제거해서 ’고양 어울림누리‘ 같은 장소와 교차어로 포함되지 않도록 함
'''
places = list(set(X_test['GUNGU']))
for i in range(len(places)):
    if places[i][-1] == '구' or places[i][-1] == '시' or places[i][-1] == '군':
        places[i] = places[i][:-1]

In [69]:
#유저가 다녀온 관광지 중에서 만족도가 4이상인 관광지 목록
recall_10_list = []
visit_list = list(info['VISIT_AREA_NM'])
for i in tqdm(list(test['TRAVEL_ID'].unique())):
    
    #추천한 방문지가 10개 미만이면 0
    if i in travel_id_list:
        recall_10_list.append(0)
        continue
    
    satisfied = test[test['TRAVEL_ID'] == i] #실제(y_actual) 관광객이 만족한 관광지
    satisfied.reset_index(drop = True, inplace = True) 
    '''
    #2회 이상 방문한 곳에 대해서만 확인
    for c in range(len(satisfied)):
        if satisfied['VISIT_AREA_NM'][c] not in visit_list:
            satisfied = satisfied.drop([c], axis = 0)
    satisfied.reset_index(drop = True, inplace = True)    
    if len(satisfied) == 0:
        recall_10_list.append(0)
        continue
    '''
    satisfied1 = satisfied[satisfied['DGSTFN'] >=4 ] #만족의 기준은 4이상 일때만 만족이라고 정의
    if len(satisfied1) == 0: # 유저가 만족한 관광지가 하나도 없으면 recall@10은 어차피 0
        recall_10_list.append(0)
        continue
    else:
        item_list = satisfied1['VISIT_AREA_NM']
                
                
    item_list = list(set(item_list))
    

#final_df의 추천지 10개랑 비교
    recommend_list = final_df[final_df['TRAVEL_ID'] == i]['recommend_result_place'] #모델 추천 관광지 30개

    summ = 0
    for n in item_list:
        word_list = list(n.split(' '))
        if word_list[-1][-1] == '점': #지점명 삭제
            del word_list[-1]
        for o in word_list:
            if o in places:#장소에 군/구 명 있으면 아무것도 하지 않고 스킵
                pass
            else:
                for p in recommend_list: #장소에 교차어 있으면 해당 장소는 방문했다고 인식하기
                    if o in str(p) :
                        summ += 1
    recall10_for_1user = summ / min(10, len(satisfied1)) #recall@10 산식
    if recall10_for_1user > 1:
        recall10_for_1user = 1
    recall_10_list.append(recall10_for_1user)

100%|██████████| 2110/2110 [00:03<00:00, 549.36it/s]


In [70]:
#recall@10 구하기 
np.mean(recall_10_list)

0.2615600315955766

In [71]:
recall_10_list

[1.0,
 1.0,
 0.5,
 0,
 1.0,
 0,
 0.0,
 0.25,
 0,
 1.0,
 1.0,
 0.0,
 0.6666666666666666,
 0.75,
 0,
 0.0,
 0,
 0.5,
 0.5,
 0.0,
 1.0,
 0.0,
 0,
 0,
 0.0,
 0.0,
 0.5,
 0.0,
 1,
 0,
 0.0,
 0.25,
 1.0,
 1.0,
 0.0,
 0.0,
 0.0,
 1,
 0.0,
 0,
 1.0,
 0,
 1.0,
 0.0,
 0.0,
 1.0,
 0,
 0.0,
 0.0,
 0.2,
 0.0,
 0.6666666666666666,
 0.3333333333333333,
 0.5,
 0,
 1.0,
 0.0,
 0,
 0.0,
 1.0,
 1.0,
 1.0,
 1.0,
 0.5,
 0.5,
 0.0,
 0,
 0,
 0.5,
 0,
 1.0,
 0,
 1.0,
 0.0,
 1,
 1,
 0,
 1.0,
 0.0,
 1.0,
 1.0,
 1.0,
 1.0,
 0.5,
 0.0,
 1.0,
 0.3333333333333333,
 0,
 0,
 0.0,
 0.0,
 0.5,
 0,
 0,
 0,
 0,
 1.0,
 0,
 0,
 0.0,
 1.0,
 0.0,
 1.0,
 1,
 1,
 0.6666666666666666,
 0.0,
 0.0,
 1,
 0,
 1,
 0,
 1.0,
 0,
 0,
 0.6,
 1.0,
 1.0,
 1.0,
 1.0,
 0,
 0,
 0.0,
 1,
 0,
 1.0,
 0.3333333333333333,
 0.0,
 1.0,
 0.0,
 1.0,
 1.0,
 0,
 0.0,
 0.0,
 0.0,
 1.0,
 0,
 0,
 0,
 0,
 1,
 1.0,
 0.0,
 0,
 0.0,
 1.0,
 0.3333333333333333,
 1,
 1.0,
 1.0,
 0.6666666666666666,
 0,
 0.0,
 0.0,
 0,
 0,
 0.0,
 0,
 1.0,
 0.0,
 1.0,
 0,
 0,
 0.5,